In [1]:
import folium
from geopy.distance import geodesic, great_circle
import geopandas as gpd
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy.spatial.distance import cdist
from shapely.ops import unary_union
import pyproj
from folium import plugins
import warnings
warnings.simplefilter("ignore")
from shapely.geometry import Polygon, MultiPolygon, Point
import re

In [2]:
df_1 = pd.read_csv("All Location - merge_IFC.csv")
df_2 = pd.read_csv(r"F:\DSLR\Folium\Animate\cc_2.csv")
df_1['Business Type'] = df_1['Business Type'].fillna('নাই')
df_2['Business Type'] = df_2['Business Type'].fillna('নাই')
df_merged = pd.read_csv(r"F:\DSLR\Folium\Animate\Projects\ifc_cc_desc.csv")
descrb = pd.read_csv(r"F:\DSLR\Folium\Animate\describe.csv")

In [3]:
up = gpd.read_file(r"F:\DSLR\Folium\Geojson\Upazilla_updated.geojson")

In [25]:
def get_div_cen(div_name):
    div_cen = {'Barisal': [22.419147168685168, 90.34719389574566],
                'Chittagong': [22.709657647813373, 91.73176862241395],
                'Dhaka': [23.839712023586152, 90.2416568363619],
                'Khulna': [22.917754757675876, 89.29251999630705],
                'Mymensingh': [24.846766716747663, 90.38045980128486],
                'Rajshahi': [24.588748960942787, 89.04457003840928],
                'Rangpur': [25.779405192595792, 89.05583622451685],
                'Sylhet': [24.71545553158574, 91.66406548888463]}
    return div_cen[div_name]

def df_process(iFc_df, cc_df, service_info, up_info, up_geo, division, district):
    div_len = len(division)
    dist_len = len(district)
    div_dist = division + '_' + district
    div_dist_len = len(div_dist)
    
    if division == 'All':
        centroid = [23.8103, 90.4125]
        zoom = 7
        return iFc_df, cc_df, service_info, up_info, up_geo, centroid, zoom
    else:
        if district == 'All':
            sort_ifc = iFc_df[iFc_df['Loc'].str[:div_len] == division].reset_index(drop=True)
            sort_cc = cc_df[cc_df['Loc'].str[:div_len] == division].reset_index(drop=True)
            sort_service = service_info[service_info.Division == division].reset_index(drop=True)
            sort_up_info = up_info[up_info.Division == division].reset_index(drop=True)
            sort_up_geo = up_geo[up_geo.ADM1_EN == division].reset_index(drop=True)
            centroid = get_div_cen(division)
            zoom = 9
        else:
            sort_ifc = iFc_df[iFc_df['Loc'].str[:div_dist_len] == div_dist].reset_index(drop=True)
            sort_cc = cc_df[cc_df['Loc'].str[:div_dist_len] == div_dist].reset_index(drop=True)
            sort_service = service_info[service_info.District == district].reset_index(drop=True)
            sort_up_info = up_info[up_info.District == district].reset_index(drop=True)
            sort_up_geo = up_geo[up_geo.ADM2_EN == district].reset_index(drop=True)
            center = sort_up_geo.unary_union.centroid
            centroid = [center.y, center.x]
            zoom = 10
    return sort_ifc, sort_cc, sort_service, sort_up_info, sort_up_geo, centroid, zoom

def dist(p1, p2):
    return round(geodesic(p1,p2).kilometers,2)

def get_fill(data, name, tooltip, clr, opacity):
    img_html = """  
        <div style="font-size: 14px">
        <img src="pie2.png" width="200" height="150">
        </div>
        """
    fill_obj = folium.GeoJson(
                    data=data,
                    name=name,
                    tooltip = tooltip,
#                     popup= folium.Popup(html= img_html),
                    style_function= style_function(clr, opacity),
                    highlight_function= lambda feat: {'fillColor': clr, 'fillOpacity': 1, 'weight': 2, 'color': clr}
                )
    
    return fill_obj

def style_function(fill_color,fill_opacity):
    return lambda feature: {
        'color': "green",
        'weight': 2,
        'fillColor': fill_color,
        'fillOpacity': fill_opacity
    }

def get_up_tt(upz, dst, ifc, cc, ifc_dist, cc_dist, ifc_cc_dist, hld):
#     image_html = '''
#     <img src="mpld3_42.png" width="200" height="150">
#     '''
    if ifc!=0 and cc!=0:
        tooltip_html = """  
        <div style="font-size: 14px">
        <b>Upazilla:</b> {up}  
        <br>
        <b>District:</b> {dist}
        <br>
        <b>iFC count:</b> {ifc}
        <br>
        <b>CC count:</b> {cc}
        <br>
        <b>Avg_iFC_dist:</b> {ifc_dist} km
        <br>
        <b>Avg_CC_dist:</b> {cc_dist} km
        <br>
        <b>Avg_iFC_CC_dist:</b> {ifc_cc_dist} km
        <br>
        <b>Total Holdings:</b> {hld}
        </div>
        """.format(up=upz, dist=dst, ifc=ifc, cc=cc, ifc_dist=ifc_dist, 
                   cc_dist=cc_dist, ifc_cc_dist=ifc_cc_dist, hld=hld)
    elif ifc==0:
        tooltip_html = """  
        <div style="font-size: 14px">
        <b>Upazilla:</b> {up}  
        <br>
        <b>District:</b> {dist}
        <br>
        <b>iFC count:</b> {ifc}
        <br>
        <b>CC count:</b> {cc}
        <br>
        <b>Avg_CC_dist:</b> {cc_dist} km
        <br>
        <b>Total Holdings:</b> {hld}
        </div>
        """.format(up=upz, dist=dst, ifc=ifc, cc=cc, cc_dist=cc_dist, hld=hld)
    
    else:
        tooltip_html = """  
        <div style="font-size: 14px">
        <b>Upazilla:</b> {up}  
        <br>
        <b>District:</b> {dist}
        <br>
        <b>iFC count:</b> {ifc}
        <br>
        <b>CC count:</b> {cc}
        <br>
        <b>Avg_iFC_dist:</b> {ifc_dist} km
        <br>
        <b>Total Holdings:</b> {hld}
        </div>
        """.format(up=upz, dist=dst, ifc=ifc, cc=cc, ifc_dist=ifc_dist, hld=hld)

    return tooltip_html

def hex_tt(bn, bt, nid, bn2, ncd, ncs, hld, srvs):

    tooltip_html = """
    <div style="font-size: 14px">
    <b>iFC Business Name:</b> {bn}
    <br>
    <b>iFC Business Type:</b> {bt}
    <br>
    <b>Service:</b> {srvs}
    <br>
    <b>Nearest iFC Distance:</b> {nid} km
    <br>
    <b>Nearest iFC Business:</b> {bn2}
    <br>
    <b>Nearest CC Distance:</b> {ncd} km
    <br>
    <b>Nearest CC Supplier:</b> {ncs}
    <br>
    <b>Holdings Covered:</b> {hld}
    </div>
    """.format(bn=bn, bt=bt, nid=nid, bn2=bn2, ncd=ncd, ncs=ncs, hld=hld, srvs=srvs)

    return tooltip_html

def hex_tt_cc(sn, bt, nid, sn2, ncd, ncb, hld):

    tooltip_html = """
    <div style="font-size: 14px">
    <b>CC Supplier Name:</b> {sn}
    <br>
    <b>CC Business Type:</b> {bt}
    <br>
    <b>Nearest CC Distance:</b> {nid} km
    <br>
    <b>Nearest CC Supplier:</b> {sn2}
    <br>
    <b>Nearest iFC Distance:</b> {ncd} km
    <br>
    <b>Nearest iFC Business:</b> {ncb}
    <br>
    <b>Holdings Covered:</b> {hld}
    </div>
    """.format(sn=sn, bt=bt, nid=nid, sn2=sn2, ncd=ncd, ncb=ncb, hld=hld)

    return tooltip_html

def hex_tt_cc_2(sn, bt, nid, sn2, ncd, ncb):

    tooltip_html = """
    <div style="font-size: 14px">
    <b>iFC Business Name:</b> {sn}
    <br>
    <b>iFC Business Type:</b> {bt}
    <br>
    <b>Nearest CC Distance:</b> {nid} km
    <br>
    <b>Nearest CC Supplier:</b> {sn2} 
    <br>
    <b>Nearest iFC Distance:</b> {ncd} km
    <br>
    <b>Nearest iFC Business:</b> {ncb}
    </div>
    """.format(sn=sn, bt=bt, nid=nid, sn2=sn2, ncd=ncd, ncb=ncb)

    return tooltip_html

def map_geo_obj(Up_df, df_processed, descrb, centroid, zoom):
    m = folium.Map(location=centroid, zoom_start=zoom, attr='Google', tiles='https://mt1.google.com/vt/lyrs=m&x={x}&y={y}&z={z}')

    for i in range(len(df_processed)):
        temp_df = Up_df[(Up_df.ADM3_EN == df_processed.Upazilla[i]) &
                        (Up_df.ADM2_EN == df_processed.District[i]) &
                        (Up_df.ADM1_EN == df_processed.Division[i])].reset_index(drop=True)

        if df_processed.iFC_no[i] == 0:
            clr = "orange"
        elif df_processed.CC_no[i] == 0:
            clr = "yellow"
        else:
            clr = "gray"
        try:
            holdings_df = descrb[(descrb.Division == df_processed.Division[i]) & 
                   (descrb.District == df_processed.District[i]) & 
                   (descrb.Upazilla == df_processed.Upazilla[i])].reset_index(drop = True)
            holdings = holdings_df["All_holdings"][0]
        except:
            holdings = 0
        
        tooltip = folium.Tooltip(get_up_tt(df_processed.Upazilla[i], df_processed.District[i],
                                          df_processed.iFC_no[i], df_processed.CC_no[i],
                                          df_processed.Avg_iFC_dist[i], df_processed.Avg_CC_dist[i],
                                          df_processed.Avg_iFC_CC_dist[i], holdings))
        Org_obj = get_fill(temp_df, df_processed.Upazilla[i], tooltip, clr, 0.4)
        Org_obj.add_to(m)
        
    return m

def poly_graph(ifc_cc_type, dataframe_1, dataframe_2, clr, rad, descrb, m):
    tt = []
    for i in range(len(dataframe_1)):
        mn = 1000
        mn_2 = 1000
        for j in range(len(dataframe_1)):
            if i!=j:
                d = dist((dataframe_1.latitude[i], dataframe_1.longitude[i]),
                         (dataframe_1.latitude[j], dataframe_1.longitude[j]))
                if d< mn:
                    mn = d
                    ind = j
            if len(dataframe_1) == 1:
                ind = 0
        for j in range(len(dataframe_2)):
            d = dist((dataframe_1.latitude[i], dataframe_1.longitude[i]),
                     (dataframe_2.latitude[j], dataframe_2.longitude[j]))
            if d< mn_2:
                mn_2 = d
                ind_2 = j
            if len(dataframe_2) == 1:
                ind_2 = 0
    #     print(mn_2)
        temp_df = descrb[(descrb.Division == dataframe_1.Loc[i].split('_')[0]) & 
               (descrb.District == dataframe_1.Loc[i].split('_')[1]) & 
               (descrb.Upazilla == dataframe_1.Loc[i].split('_')[2])].reset_index(drop = True)
        
        if ifc_cc_type == "CC":
            try:
                holdings = int(temp_df["All_holdings"][0]/temp_df["area"][0]*15752)
            except:
                holdings = 0
            tooltip = hex_tt_cc(dataframe_1["Supplier Name"][i], dataframe_1["Business Type"][i],
                                mn, dataframe_1["Supplier Name"][ind],
                                mn_2, dataframe_2["Business Name"][ind_2], holdings)
            tt.append([dataframe_1["Supplier Name"][i], dataframe_1["Business Type"][i], 
                       mn, dataframe_1["Supplier Name"][ind], mn_2, dataframe_2["Business Name"][ind_2], holdings])
        else:
            cen_clr, service = get_service(dataframe_1.Input_Exist[i], 
                                           dataframe_1.Field_Finance_Exist[i], 
                                           dataframe_1.Advisory_Exist[i])
            try:
                holdings = int(temp_df["All_holdings"][0]/temp_df["area"][0]*5671)
            except:
                holdings = 0
            tooltip = hex_tt(dataframe_1["Business Name"][i], dataframe_1["Business Type"][i],
                             mn, dataframe_1["Business Name"][ind],
                             mn_2,dataframe_2["Supplier Name"][ind_2], holdings, service)

            tt.append([dataframe_1["Business Name"][i], dataframe_1["Business Type"][i],
                       mn, dataframe_1["Business Name"][ind], mn_2,dataframe_2["Supplier Name"][ind_2], holdings])
        folium.Polygon(locations=create_polygon((dataframe_1.latitude[i], dataframe_1.longitude[i]), rad), 
                       fill_color=clr, color = clr, fillOpacity = 0.3, tooltip = tooltip).add_to(m)
    return m, tt

def get_service(Input_Exist, Field_Finance, Advisory_Exist):
    
    count = Input_Exist + Field_Finance + Advisory_Exist

    if count == 1:
        cen_clr = 'red'
        if Input_Exist == 1: 
            cen_clr = 'blue'
            service = 'Input'
            return cen_clr, service
        elif Field_Finance == 1:
            cen_clr = 'red'
            service = 'Field_Finance'
            return cen_clr, service
        else:
            service = 'Advisory'
            return cen_clr, service
    if count == 2:
        cen_clr = 'yellow'
        if Input_Exist == 0: 
            service = 'Field_Finance, Advisory'
            return cen_clr, service
        elif Field_Finance == 0:
            service = 'Input, Advisory'
            return cen_clr, service
        else:
            service = 'Input, Field_Finance'
            return cen_clr, service

    if count == 3:
        service = 'Input, Field_Finance, Advisory'
        cen_clr = 'green'
        return cen_clr, service
    

def centroid_gen(dataframe, df_type, t_tip, clr, rad, m):
    
    for i in range(len(dataframe)):
        if df_type == "CC":
            tooltip = hex_tt_cc(t_tip[i][0], t_tip[i][1], t_tip[i][2], t_tip[i][3], t_tip[i][4], t_tip[i][5], t_tip[i][6])
            cen_clr = clr
        else:
            cen_clr, service = get_service(dataframe.Input_Exist[i], 
                                           dataframe.Field_Finance_Exist[i], 
                                           dataframe.Advisory_Exist[i])
            tooltip = hex_tt(t_tip[i][0], t_tip[i][1], t_tip[i][2], 
                                 t_tip[i][3], t_tip[i][4], t_tip[i][5], t_tip[i][6], service)
        folium.Circle(location=[dataframe.latitude[i], dataframe.longitude[i]],
                          radius= rad,
                          color=cen_clr,
                          fill_color = cen_clr,
                          fillOpacity = 1,
                          tooltip = tooltip,
    #                       weight=0,
                          stroke = True).add_to(m)
    return m

def ifc_cc_df(dataframe, business_type):
    if "All" not in business_type:
        search_pattern = '|'.join(business_type)
        return dataframe[dataframe['Business Type'].str.contains(search_pattern, regex=True)].reset_index(drop=True)
    else:
        return dataframe
    
def create_polygon(centre, radius_km, num_points=6):
    polygon = []

    for i in range(num_points):
        angle = 360.0 * i / num_points
        point = geodesic(kilometers=radius_km).destination(centre, angle)
        polygon.append((point.latitude, point.longitude))
#         print(dist(centre, polygon[i]))

    polygon.append(polygon[0])
    return polygon

def filter_info_df(df_type, df_merged, dataframe_1, dataframe_2):
    if df_type == "All":
        df_merged_processed = df_merged[((df_merged.Division + "_" + df_merged.District + "_" + df_merged.Upazilla).isin(dataframe_2.Loc)) |
                                       ((df_merged.Division + "_" + df_merged.District + "_" + df_merged.Upazilla).isin(dataframe_1.Loc))].reset_index(drop = True)
    elif df_type == "CC":
        df_merged_processed = df_merged[(df_merged.Division + "_" + df_merged.District + "_" + df_merged.Upazilla).isin(dataframe_2.Loc)].reset_index(drop = True)
    elif df_type == "iFC":
        df_merged_processed = df_merged[(df_merged.Division + "_" + df_merged.District + "_" + df_merged.Upazilla).isin(dataframe_1.Loc)].reset_index(drop = True)
    return df_merged_processed

def get_legend(df_type):
    if df_type == 'iFC':
        legendHtml_1 = '''
            <div style="position: fixed; 
            bottom: 50px; left: 50px; width: 150px; height: 120px; 
            border:2px solid grey; z-index:9999; font-size:14px; background-color: white; display: flex};
            ">
            &nbsp; Description <br>
            &nbsp; <i class="fa fa-circle" style="color:blue"></i> &nbsp; Input<br>
            &nbsp; <i class="fa fa-circle" style="color:red"></i> &nbsp; Field Finance<br>
            &nbsp; <i class="fa fa-circle" style="color:yellow"></i> &nbsp; Two Services<br>
            &nbsp; <i class="fa fa-circle" style="color:green"></i> &nbsp; All Services<br>
            </div>
            '''
    if df_type == 'CC':
        legendHtml_1 = '''
            <div style="position: fixed; 
            bottom: 50px; left: 50px; width: 160px; height: 60px; 
            border:2px solid grey; z-index:9999; font-size:14px; background-color: white; display: flex};
            ">
            &nbsp; Description <br>
            &nbsp; <i class="fa fa-circle" style="color:magenta"></i> &nbsp; Collection Center<br>
            </div>
            '''
    if df_type == 'All':
        legendHtml_1 = '''
            <div style="position: fixed; 
            bottom: 50px; left: 50px; width: 160px; height: 130px; 
            border:2px solid grey; z-index:9999; font-size:14px; background-color: white; display: flex};
            ">
            &nbsp; Description <br>
            &nbsp; <i class="fa fa-circle" style="color:blue"></i> &nbsp; Input<br>
            &nbsp; <i class="fa fa-circle" style="color:red"></i> &nbsp; Field Finance<br>
            &nbsp; <i class="fa fa-circle" style="color:yellow"></i> &nbsp; Two Services<br>
            &nbsp; <i class="fa fa-circle" style="color:green"></i> &nbsp; All Services<br>
            &nbsp; <i class="fa fa-circle" style="color:magenta"></i> &nbsp; Collection Center<br>
            </div>
            '''
    return legendHtml_1

In [26]:
def init(df_type, dframe_1, dframe_2, df_merged, descrb, up_df, division, district, ifc_buss = ["All"], cc_buss = ["All"]):
    sort_ifc, sort_cc, sort_service, sort_up_info, sort_up_geo, centroid, zoom = df_process(dframe_1, dframe_2, 
                                                                                            df_merged, descrb, 
                                                                                            up_df, division, district)
#     if (len(sort_ifc) + len(sort_cc)) == 0:
#         return 'Not_found'
    dataframe_1 = ifc_cc_df(sort_ifc, ifc_buss)
    dataframe_2 = ifc_cc_df(sort_cc, cc_buss)
    df_merged_processed = filter_info_df(df_type, sort_service, dataframe_1, dataframe_2)
    m = map_geo_obj(sort_up_geo, df_merged_processed, sort_up_info, centroid, zoom)
    if (df_type == "CC") or (df_type == "All"):
        m, tt_cc = poly_graph("CC", dataframe_2, dframe_1, "purple", 5, sort_up_info, m)
    if (df_type == "iFC") or (df_type == "All"):
        m, tt_ifc = poly_graph("iFC", dataframe_1, dframe_2, "blue", 3, sort_up_info, m)
    if (df_type == "iFC") or (df_type == "All"):
        m = centroid_gen(dataframe_1, "iFC", tt_ifc, "blue", 400, m)
    if (df_type == "CC") or (df_type == "All"):
        m = centroid_gen(dataframe_2, "CC", tt_cc, "magenta", 300, m)
    
    legendHtml = get_legend(df_type)
    m.get_root().html.add_child(folium.Element(legendHtml))
    return m

In [31]:
m = init("All", df_1, df_2, df_merged, descrb, up, 'Rajshahi', "All", ['ফিড', 'সার'], ['ধান', 'গরু'])
m

In [7]:
# df_2['Business Type'].unique()

In [8]:
# ifc_business =  কীটনাশক, বীজ, সার, ফিড, ALL
# cc_business = ভূট্টা, ধান, পাট, সরিষা, শাক-সবজি, গরু, মাছ, শস্য, ছাগল, মুরগি, ফলমূল, মরিচ, পেয়াজ, 'ALL'

In [9]:
# ifc = pd.read_csv("All Location - merge_IFC.csv")

# li_fin = []
# li_inp = []

# for i in range(len(ifc)):
#     if ifc.Field_Finance_Exist[i] == 1:
#         for j in range(len(ifc)):
#             if ifc.Input_Exist[j] == 1:
#                 if i!=j:
#                     d = dist((ifc.latitude[i], ifc.longitude[i]),
#                              (ifc.latitude[j], ifc.longitude[j]))
#                     if d < 1:
#                         li_fin.append([ifc.Sl[i], ifc.Sl[j], d])
# #                         li_inp.append(ifc.Sl[j])

In [10]:
# li_fin

In [11]:
# li_inp

In [12]:
# ifc[ifc.Sl.isin(li_inp)].reset_index(drop=True)

In [15]:
ifc_cc_df(df_1,['সার', 'ফিড'])

Sl Regional ifarmer Office          TO Officer  \
0    1   Bogura ifarmer Office        মামুনুর রশিদ   
1    2   Bogura ifarmer Office        মনিরুজ্জামান   
2    3   Bogura ifarmer Office          সুজন রহমান   
3    4   Bogura ifarmer Office        মনিরুজ্জামান   
4    5   Bogura ifarmer Office         নাজমুল হূদা   
..  ..                     ...                 ...   
82  89  Rangpur ifarmer Office              Mondol   
83  90  Rangpur ifarmer Office  শামছুল ইসলাম শাহেদ   
84  91  Rangpur ifarmer Office       মোঃ রতন মিয়া   
85  92  Rangpur ifarmer Office          আব্দুর নূর   
86  93   Bogura ifarmer Office          আব্দুর নূর   

                 Business Name          Owner Name  Owner Phone  \
0             Abdullah Traders     Nuruzzaman tota   1784552982   
1              Suvo enterprise  Arman Hossen Liton   1740545616   
2              কে আর ট্রেডার্স         জামাল আহমেদ   1711413823   
3                Mabia Traders   Saiduzzaman Hiron   1724860854   
4             jihad enterprise               jahid   1724592718   
..                         ...                 ...          ...   
82  মেসার্স আইমান ফার্টিলাইজার        নুর আলম মিয়া   1734676159   
83                   রতন স্টোর             মোঃ রতন   1748737762   
84        মেসার্স আনিস ট্রেডাস                আনিস   1700538467   
85   মেসার্স সানজিদা ট্রেডার্স      মোঃ খোরশেদ আলম   1738161682   
86     মেসার্স মন্ডল ট্রেডার্স   মোঃ শাজাহান মন্ডল   1724104417   

                                  Business Address Division    District  \
0                                     Gohail bajar  রাজশাহী       বগুড়া   
1                                     Noy mail hat  রাজশাহী       বগুড়া   
2                                        দক্ষিনভাগ  রাজশাহী       বগুড়া   
3                               Jamail Hat sherpur  রাজশাহী       বগুড়া   
4                            mondolmor pabna sadar  রাজশাহী       পাবনা   
..                                             ...      ...         ...   
82                          বড়ভিটা, বড়ভিটা, বড়ভিটা    রংপুর  কুড়িগ্রাম   
83        চাকগৌরি বাজার গ্রাম পাতনা ভীমপুর ইউনিয়ন  রাজশাহী       নওগাঁ   
84  কদমতলী বাজার, কাশিবাড়ী কৃষ্ণাপুর এবং চেরাগপুর  রাজশাহী       নওগাঁ   
85            ডাইমুল্লাহঘাট,পলিকাদোয়া সদর জয়পুরহাট  রাজশাহী   জয়পুরহাট   
86                        হিচমী বাজার সদর জয়পুরহাট  রাজশাহী   জয়পুরহাট   

          Upazila    Business Type  Input_Exist  Field_Finance_Exist  \
0      শাজাহানপুর  কীটনাশক বীজ সার            1                    1   
1      শাজাহানপুর  কীটনাশক বীজ সার            1                    1   
2       বগুড়া সদর  কীটনাশক বীজ সার            1                    1   
3          শেরপুর  কীটনাশক বীজ সার            1                    1   
4       পাবনা সদর      কীটনাশক সার            1                    1   
..            ...              ...          ...                  ...   
82       ফুলবাড়ী  কীটনাশক বীজ সার            1                    1   
83      মহাদেবপুর              ফিড            1                    0   
84      মহাদেবপুর              ফিড            1                    0   
85  জয়পুরহাট সদর  কীটনাশক বীজ সার            1                    1   
86  জয়পুরহাট সদর  কীটনাশক বীজ সার            1                    1   

    Advisory_Exist   latitude  longitude                                 Loc  
0                1  24.725037  89.318024          Rajshahi_Bogra_Shajahanpur  
1                1  24.725516  89.397543          Rajshahi_Bogra_Shajahanpur  
2                0  24.941189  89.372070          Rajshahi_Bogra_Bogra Sadar  
3                1  24.611999  89.362524              Rajshahi_Bogra_Sherpur  
4                0  24.007720  89.160668          Rajshahi_Pabna_Pabna Sadar  
..             ...        ...        ...                                 ...  
82               1  25.908081  89.581306           Rangpur_Kurigram_Phulbari  
83               0  24.858411  88.865216         Rajshahi_Naogaon_Mahadebpur  
84               0  24.872751  88.823542         Rajshahi_Naogaon_Mahadeb

In [12]:
search_pattern

'কীটনাশক'

In [29]:
df_2['Business Type'].unique()

array(['ভূট্টা', 'ধান', 'ধান পাট সরিষা', 'ধান পাট', 'ধান সরিষা',
       'শাক-সবজি', 'গরু', 'শাক-সবজি মাছ', 'মাছ', 'ধান পাট শস্য',
       'ধান সরিষা গরু ছাগল', 'মুরগি', 'ধান পাট শাক-সবজি', 'ফলমূল',
       'শাক-সবজি মরিচ', 'পাট পেয়াজ ধান', 'পাট পেয়াজ', 'সরিষা',
       'গরু ধান পাট', 'গরু শাক-সবজি ধান', 'পাট', 'শস্য', 'শাক-সবজি ফলমূল',
       'ছাগল'], dtype=object)

In [24]:
df_1

Sl  Regional ifarmer Office    TO Officer          Business Name  \
0      1    Bogura ifarmer Office  মামুনুর রশিদ       Abdullah Traders   
1      2    Bogura ifarmer Office  মনিরুজ্জামান        Suvo enterprise   
2      3    Bogura ifarmer Office    সুজন রহমান        কে আর ট্রেডার্স   
3      4    Bogura ifarmer Office  মনিরুজ্জামান          Mabia Traders   
4      5    Bogura ifarmer Office   নাজমুল হূদা       jihad enterprise   
..   ...                      ...           ...                    ...   
122  129  Jamalpur ifarmer Office           NaN   M/S Taiaba Fish Feed   
123  130   Rangpur ifarmer Office           NaN      Ma Babar Ashirbad   
124  131   Rangpur ifarmer Office           NaN       MS Vupak Traders   
125  132   Jashore ifarmer Office           NaN    M/S Bhai Bhai store   
126  133   Jashore ifarmer Office           NaN  M/S. Riyad Enterprise   

               Owner Name  Owner Phone                       Business Address  \
0         Nuruzzaman tota   1784552982                           Gohail bajar   
1      Arman Hossen Liton   1740545616                           Noy mail hat   
2             জামাল আহমেদ   1711413823                              দক্ষিনভাগ   
3       Saiduzzaman Hiron   1724860854                     Jamail Hat sherpur   
4                   jahid   1724592718                  mondolmor pabna sadar   
..                    ...          ...                                    ...   
122      Md. Anowar Hosen   1729689408  Khukshiabazar, Kumargatha, Mymenshing   
123              Hriodayo   1744355644      Balubaribazar,Pirgonj, Thakurgaon   
124  Shashi Vushon Sarker   1645537846          Sobandaha,patershori,Kurigram   
125      Md. atiar Rahman   1745308172  kapalia,Monohorpur,Monirampur,Jashore   
126         Md.golam Nobi   1712359989      Berbari,Paglakani,Sadar,Jhenaidah   

     Division   District     Upazila    Business Type  Input_Exist  \
0     রাজশাহী      বগুড়া  শাজাহানপুর  কীটনাশক বীজ সার            1   
1     রাজশাহী      বগুড়া  শাজাহানপুর  কীটনাশক বীজ সার            1   
2     রাজশাহী      বগুড়া   বগুড়া সদর  কীটনাশক বীজ সার            1   
3     রাজশাহী      বগুড়া      শেরপুর  কীটনাশক বীজ সার            1   
4     রাজশাহী      পাবনা   পাবনা সদর      কীটনাশক সার            1   
..        ...        ...         ...              ...          ...   
122  ময়মনসিংহ   ময়মনসিংহ         NaN              নাই            0   
123   রাজশাহী  ঠাকুরগাঁও         NaN              নাই            0   
124   রাজশাহী  কুড়িগ্রাম         NaN              নাই            0   
125     খুলনা       যশোর         NaN              নাই            0   
126     খুলনা    ঝিনাইদহ         NaN              নাই            0   

     Field_Finance_Exist  Advisory_Exist   latitude  longitude  \
0                      1               1  24.725037  89.318024   
1                      1               1  24.725516  89.397543   
2                      1               0  24.941189  89.372070   
3                      1               1  24.611999  89.362524   
4                      1               0  24.007720  89.160668   
..                   ...             ...        ...        ...   
122                    1               0  24.766161  90.255818   
123                    1               1  25.861359  88.361881   
124                    1               0  25.856089  89.671921   
125                    1               1  22.947030  89.319939   
126                    1               1  23.535721  89.154452   

                                   Loc  
0           Rajshahi_Bogra_Shajahanpur  
1           Rajshahi_Bogra_Shajahanpur  
2           Rajshahi_Bogra_Bogra Sadar  
3               Rajshahi_Bogra_Sherpur  
4           Rajshahi_Pabna_Pabna Sadar  
..                                 ...  
122  Mymensingh_Mymensingh_Muktagachha  
123         Rangpur_Thakurgaon_Pirganj  
124    Rangpur_Kurigram_Kurigram Sadar  
125          Khulna_Jessore_Manirampur  
126   Khulna_Jhenaidah_Jhenaidah Sadar  

[127 rows x 17 co